## Import Packages

In [1]:
import os
os.chdir("..")

import warnings
warnings.filterwarnings("ignore")

In [2]:
import torch
from transformers import GenerationConfig, LlamaTokenizer, LlamaForCausalLM
from peft import PeftModel, PeftConfig


===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please run

python -m bitsandbytes

 and submit this information together with your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
bin /opt/conda/envs/media-reco-env-3-8/lib/python3.8/site-packages/bitsandbytes/libbitsandbytes_cuda112_nocublaslt.so
CUDA_SETUP: WARNING! libcudart.so not found in any environmental path. Searching in backup paths...
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 7.0
CUDA SETUP: Detected CUDA version 112
CUDA SETUP: Loading binary /opt/conda/envs/media-reco-env-3-8/lib/python3.8/site-packages/bitsandbytes/libbitsandbytes_cuda112_nocublaslt.so...


## Utilities

In [3]:
def generate_prompt(instruction: str, input_ctxt: str = None) -> str:
    if input_ctxt:
        return f"""Below is an instruction that describes a task, paired with an input that provides further context. Write a response that appropriately completes the request.

### Instruction:
{instruction}

### Input:
{input_ctxt}

### Response:"""
    else:
        return f"""Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
{instruction}

### Response:"""

## Configs

In [4]:
MODEL_NAME = "."
BASE_MODEL = "decapoda-research/llama-13b-hf"
LOAD_FINETUNED = False

## Load Model & Tokenizer

In [5]:
config = PeftConfig.from_pretrained(MODEL_NAME)

tokenizer = LlamaTokenizer.from_pretrained(MODEL_NAME)

model = LlamaForCausalLM.from_pretrained(
    BASE_MODEL,
    load_in_8bit=True,
    torch_dtype=torch.float16,
    device_map="auto",
)
    
# model.eval()
# if torch.__version__ >= "2":
#     model = torch.compile(model)

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


Loading checkpoint shards:   0%|          | 0/41 [00:00<?, ?it/s]

## Generation Examples

In [6]:
generation_config = GenerationConfig(
    temperature=0.2,
    top_p=0.95,
    top_k=40,
    num_beams=4,
    max_new_tokens=50,
    repetition_penalty=1.7,
)

## Examples with Base (decapoda-research/llama-7b-hf) model

### Example 1

In [7]:
instruction = "I have two pieces of apples and 3 pieces of oranges. How many pieces of fruits do I have?"
input_ctxt = None  # For some tasks, you can provide an input context to help the model generate a better response.

prompt = generate_prompt(instruction, input_ctxt)
input_ids = tokenizer(prompt, return_tensors="pt").input_ids
input_ids = input_ids.to(model.device)

with torch.no_grad():
    outputs = model.generate(
        input_ids=input_ids,
        generation_config=generation_config,
        return_dict_in_generate=True,
        output_scores=True,
    )

response = tokenizer.decode(outputs.sequences[0], skip_special_tokens=True)
print(response)

Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
I have two pieces of apples and 3 pieces of oranges. How many pieces of fruits do I have?

### Response:


### Example 2

In [8]:
instruction = "What is the capital city of Greece and with which countries does Greece border?"
input_ctxt = None  # For some tasks, you can provide an input context to help the model generate a better response.

prompt = generate_prompt(instruction, input_ctxt)
input_ids = tokenizer(prompt, return_tensors="pt").input_ids
input_ids = input_ids.to(model.device)

with torch.no_grad():
    outputs = model.generate(
        input_ids=input_ids,
        generation_config=generation_config,
        return_dict_in_generate=True,
        output_scores=True,
    )

response = tokenizer.decode(outputs.sequences[0], skip_special_tokens=True)
print(response)

Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
What is the capital city of Greece and with which countries does Greece border?

### Response: The capital city of Greece is Athens, and it borders Albania, Bulgaria, Macedonia, and Turkey.

## See also

* Natural language processing
* Question answering

## External links

* Official website


### Example 3

In [9]:
instruction = "Como cocinar supa de pescado?"
input_ctxt = None  # For some tasks, you can provide an input context to help the model generate a better response.

prompt = generate_prompt(instruction, input_ctxt)
input_ids = tokenizer(prompt, return_tensors="pt").input_ids
input_ids = input_ids.to(model.device)

with torch.no_grad():
    outputs = model.generate(
        input_ids=input_ids,
        generation_config=generation_config,
        return_dict_in_generate=True,
        output_scores=True,
    )

response = tokenizer.decode(outputs.sequences[0], skip_special_tokens=True)
print(response)

Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
Como cocinar supa de pescado?

### Response: 
¿Cómo se prepara la sopa de pescado?

## See also

* Spanish orthography
* Spanish phonology


### Example 4

In [10]:
instruction = "Which are the tags of the following article: 'A year ago, Russia invaded Ukraine in a major escalation of the Russo-Ukrainian War, which had begun in 2014. The invasion has resulted in thousands of deaths, and instigated Europe's largest refugee crisis since World War II.'?"
input_ctxt = None  # For some tasks, you can provide an input context to help the model generate a better response.

prompt = generate_prompt(instruction, input_ctxt)
input_ids = tokenizer(prompt, return_tensors="pt").input_ids
input_ids = input_ids.to(model.device)

with torch.no_grad():
    outputs = model.generate(
        input_ids=input_ids,
        generation_config=generation_config,
        return_dict_in_generate=True,
        output_scores=True,
    )

response = tokenizer.decode(outputs.sequences[0], skip_special_tokens=True)
print(response)

Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
Which are the tags of the following article: 'A year ago, Russia invaded Ukraine in a major escalation of the Russo-Ukrainian War, which had begun in 2014. The invasion has resulted in thousands of deaths, and instigated Europe's largest refugee crisis since World War II.'?

### Response: A year ago, Russia invaded Ukraine in a major escalation of the Russo-Ukrainian War, which had begun in 2014. The invasion has resulted in thousands of deaths, and instigated Europe


### Example 5

In [11]:
instruction = "Ποιά είναι η μεγαλύτερη πόλη της Ελλάδας?"
input_ctxt = None  # For some tasks, you can provide an input context to help the model generate a better response.

prompt = generate_prompt(instruction, input_ctxt)
input_ids = tokenizer(prompt, return_tensors="pt").input_ids
input_ids = input_ids.to(model.device)

with torch.no_grad():
    outputs = model.generate(
        input_ids=input_ids,
        generation_config=generation_config,
        return_dict_in_generate=True,
        output_scores=True,
    )

response = tokenizer.decode(outputs.sequences[0], skip_special_tokens=True)
print(response)

Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
Ποιά είναι η μεγαλύτερη πόλη της Ελλάδας?

### Response: The largest city in Greece is Thessaloniki.

### Instruction:
Ποιά είναι η μεγαλύτερη πόλη τ


## Examples with Fine-Tuned model

## Let's Load the Fine-Tuned version

In [12]:
model = PeftModel.from_pretrained(model, MODEL_NAME)

### Example 1

In [13]:
instruction = "I have two pieces of apples and 3 pieces of oranges. How many pieces of fruits do I have?"
input_ctxt = None  # For some tasks, you can provide an input context to help the model generate a better response.

prompt = generate_prompt(instruction, input_ctxt)
input_ids = tokenizer(prompt, return_tensors="pt").input_ids
input_ids = input_ids.to(model.device)

with torch.no_grad():
    outputs = model.generate(
        input_ids=input_ids,
        generation_config=generation_config,
        return_dict_in_generate=True,
        output_scores=True,
    )

response = tokenizer.decode(outputs.sequences[0], skip_special_tokens=True)
print(response)

Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
I have two pieces of apples and 3 pieces of oranges. How many pieces of fruits do I have?

### Response: depends on what you mean by "pieces of fruits". If you mean individual pieces of fruit, then you have 5 pieces of fruit (2 apples and 3 oranges). If you mean slices of fruit, then you have


### Example 2

In [14]:
instruction = "What is the capital city of Greece and with which countries does Greece border?"
input_ctxt = None  # For some tasks, you can provide an input context to help the model generate a better response.

prompt = generate_prompt(instruction, input_ctxt)
input_ids = tokenizer(prompt, return_tensors="pt").input_ids
input_ids = input_ids.to(model.device)

with torch.no_grad():
    outputs = model.generate(
        input_ids=input_ids,
        generation_config=generation_config,
        return_dict_in_generate=True,
        output_scores=True,
    )

response = tokenizer.decode(outputs.sequences[0], skip_special_tokens=True)
print(response)

Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
What is the capital city of Greece and with which countries does Greece border?

### Response:'Athens is the capital city of Greece. Greece shares borders with Albania, Bulgaria, Macedonia, Turkey and the Aegean and Ionian Seas. '


### Example 3

In [15]:
instruction = "Como cocinar supa de pescado?"
input_ctxt = None  # For some tasks, you can provide an input context to help the model generate a better response.

prompt = generate_prompt(instruction, input_ctxt)
input_ids = tokenizer(prompt, return_tensors="pt").input_ids
input_ids = input_ids.to(model.device)

with torch.no_grad():
    outputs = model.generate(
        input_ids=input_ids,
        generation_config=generation_config,
        return_dict_in_generate=True,
        output_scores=True,
    )

response = tokenizer.decode(outputs.sequences[0], skip_special_tokens=True)
print(response)

Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
Como cocinar supa de pescado?

### Response:ambos tipos de supa de pescado pueden ser cocinados en el horno o en una olla de cocina. Para preparar la supa de pescado en el horno, simplemente col


### Example 4

In [16]:
instruction = "Which are the tags of the following article: 'A year ago, Russia invaded Ukraine in a major escalation of the Russo-Ukrainian War, which had begun in 2014. The invasion has resulted in thousands of deaths, and instigated Europe's largest refugee crisis since World War II.'?"
input_ctxt = None  # For some tasks, you can provide an input context to help the model generate a better response.

prompt = generate_prompt(instruction, input_ctxt)
input_ids = tokenizer(prompt, return_tensors="pt").input_ids
input_ids = input_ids.to(model.device)

with torch.no_grad():
    outputs = model.generate(
        input_ids=input_ids,
        generation_config=generation_config,
        return_dict_in_generate=True,
        output_scores=True,
    )

response = tokenizer.decode(outputs.sequences[0], skip_special_tokens=True)
print(response)

Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
Which are the tags of the following article: 'A year ago, Russia invaded Ukraine in a major escalation of the Russo-Ukrainian War, which had begun in 2014. The invasion has resulted in thousands of deaths, and instigated Europe's largest refugee crisis since World War II.'?

### Response: is a news article about the Russo-Ukrainian War. It was published on February 24, 2022, by The New York Times. Here are the tags of the article:

### Instruction


### Example 5

In [17]:
instruction = "Ποιά είναι η μεγαλύτερη πόλη της Ελλάδας?"
input_ctxt = None  # For some tasks, you can provide an input context to help the model generate a better response.

prompt = generate_prompt(instruction, input_ctxt)
input_ids = tokenizer(prompt, return_tensors="pt").input_ids
input_ids = input_ids.to(model.device)

with torch.no_grad():
    outputs = model.generate(
        input_ids=input_ids,
        generation_config=generation_config,
        return_dict_in_generate=True,
        output_scores=True,
    )

response = tokenizer.decode(outputs.sequences[0], skip_special_tokens=True)
print(response)

Below is an instruction that describes a task. Write a response that appropriately completes the request.

### Instruction:
Ποιά είναι η μεγαλύτερη πόλη της Ελλάδας?

### Response:'
Η Αθήνα είναι η μεγαλύτερη πόλη της Ελλάδας και 
